<a href="https://colab.research.google.com/github/natdebandi/hate_speech_ar/blob/main/2_GPT_evaluate_batch.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# TP final - reconocimiento de discursos discriminatorios en Twitter

Esta notebook se usa para recuperar los batch de GPT y evaluarlos en relación a los datos de test

**Natalia Dedandi**





La documentación de la API se encuentra aqui:

https://platform.openai.com/docs/api-reference/introduction



In [2]:
pip install openai

In [3]:
!pip install datasets seaborn


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 14.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 9.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 15.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.5 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.31.0
    Uninstalling requests-2.31.0:
      Successfully uninstalled requests-2.31.0
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requir

In [5]:
import json
from openai import OpenAI
import os
from google.colab import userdata
#seteo la KEY
os.environ['OPENAI_API_KEY'] = userdata.get('openIA_key')




In [6]:
#creo el cliente OPENAI con mi usuario y proyecto
client = OpenAI(
  organization='org-1uHjwiaB3OlPzoxfVzhqOSzs',
  project='proj_2fII7izwVGgYaERNNKhhMx4l',
)

Debo cargar mi dataset de TEST y pasarle un archivo BATCH para que lo procese

Usare este mensaje para cada Tweet:

"role": "system", "content": "You are trained to analyze and detect the sentiment of the given text. Only hateful or not hateful is allowed. The answer should be in spanish"

In [7]:
from datasets import load_dataset
import pandas as pd

ds1 = load_dataset("piuba-bigdata/contextualized_hate_speech")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/36420 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11343 [00:00<?, ? examples/s]

Generating dev split:   0%|          | 0/9106 [00:00<?, ? examples/s]

In [8]:
ds1

DatasetDict({
    train: Dataset({
        features: ['id', 'title', 'text', 'context_tweet', 'HATEFUL', 'body', 'CALLS', 'WOMEN', 'LGBTI', 'RACISM', 'CLASS', 'POLITICS', 'DISABLED', 'APPEARANCE', 'CRIMINAL'],
        num_rows: 36420
    })
    test: Dataset({
        features: ['id', 'title', 'text', 'context_tweet', 'HATEFUL', 'body', 'CALLS', 'WOMEN', 'LGBTI', 'RACISM', 'CLASS', 'POLITICS', 'DISABLED', 'APPEARANCE', 'CRIMINAL'],
        num_rows: 11343
    })
    dev: Dataset({
        features: ['id', 'title', 'text', 'context_tweet', 'HATEFUL', 'body', 'CALLS', 'WOMEN', 'LGBTI', 'RACISM', 'CLASS', 'POLITICS', 'DISABLED', 'APPEARANCE', 'CRIMINAL'],
        num_rows: 9106
    })
})

In [9]:

df_test = pd.DataFrame(ds1['test'])
df_test

id                                              title  \
0      397703  Mora Godoy cierra su escuela de tango y remata...   
1      397704  Mora Godoy cierra su escuela de tango y remata...   
2      397705  Mora Godoy cierra su escuela de tango y remata...   
3      397706  Mora Godoy cierra su escuela de tango y remata...   
4      397707  Mora Godoy cierra su escuela de tango y remata...   
...       ...                                                ...   
11338  361071  Nahir Galarza sumó a una abogada feminista a s...   
11339  361072  Nahir Galarza sumó a una abogada feminista a s...   
11340  361073  Nahir Galarza sumó a una abogada feminista a s...   
11341  361074  Nahir Galarza sumó a una abogada feminista a s...   
11342  361075  Nahir Galarza sumó a una abogada feminista a s...   

                                                    text  \
0              @usuario Ojalá se funda y cague de hambre   
1      @usuario Faltó que se enganchó al hijo de sofo...   
2      @usuario y bue, que le vaya a llorar a Cristin...   
3      @usuario @usuario Jodete. Macri te hizo conoce...   
4      @usuario Que se joda, es su gobierno el que el...   
...                                                  ...   
11338  @usuario Con esa varita q no rompe un plato ni...   
11339  @usuario No las entiendo a estas pelotudas. So...   
11340                 @usuario Lo mató por qué es macho!   
11341  @usuario Cuando sos asesina tenés que hacerte ...   
11342  @usuario La quieren liberar a toda costa a est...   

                                           context_tweet  HATEFUL  \
0      Mora Godoy cierra su escuela de tango y remata...        0   
1      Mora Godoy cierra su escuela de tango y remata...        1   
2      Mora Godoy cierra su escuela de tango y remata...        0   
3      Mora Godoy cierra su escuela de tango y remata...        0   
4      Mora Godoy cierra su escuela de tango y remata...        0   
...                                                  ...      ...   
11338  Nahir Galarza sumó a una abogada feminista a s...        0   
11339  Nahir Galarza sumó a una abogada feminista a s...        1   
11340  Nahir Galarza sumó a una abogada feminista a s...        0   
11341  Nahir Galarza sumó a una abogada feminista a s...        0   
11342  Nahir Galarza sumó a una abogada feminista a s...        1   

                                                    body  CALLS  WOMEN  LGBTI  \
0      Puede marcar con justeza la fecha de inicio de...      0      0      0   
1      Puede marcar con justeza la fecha de inicio de...      0      1      0   
2      Puede marcar con justeza la fecha de inicio de...      0      0      0   
3      Puede marcar con justeza la fecha de inicio de...      0      0      0   
4      Puede marcar con justeza la fecha de inicio de...      0      0      0   
...                                                  ...    ...    ...    ...   
11338  La defensa de Nahir Galarza, condenada el 3 de...      0      0      0   
11339  La defensa de Nahir Galarza, condenada el 3 de...      0      1      0   
11340  La defensa de Nahir Galarza, condenada el 3 de...      0      0      0   
11341  La defensa de Nahir Galarza, condenada el 3 de...      0      0      0   
11342  La defensa de Nahir Galarza, condenada el 3 de...      0      1      0   

       RACISM  CLASS  POLITICS  DISABLED  APPEARANCE  CRIMINAL  
0           0      0         0         0           0         0  
1           0      0         0         0           0         0  
2           0      0         0         0           0         0  
3           0      0         0         0           0         0  
4           0      0         0         0           0         0  
...       ...    ...       ...       ...         ...       ...  
11338       0      0         0         0           0         0  
11339       0      0         0         0           0         0  
11340       0      0         0         0           0         0  
11341       0      0 

In [10]:
client.batches.list(limit=10)


SyncCursorPage[Batch](data=[Batch(id='batch_RgCzgFJMbDxH1Hu0wEdKTWEq', completion_window='24h', created_at=1721929190, endpoint='/v1/chat/completions', input_file_id='file-p3GRq3qXolsAdETkRL4z96WH', object='batch', status='failed', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=Errors(data=[BatchError(code='token_limit_exceeded', line=None, message='Enqueued token limit reached for gpt-4o-mini in organization org-1uHjwiaB3OlPzoxfVzhqOSzs. Limit: 2,000,000 enqueued tokens. Please try again once some in_progress batches have been completed.', param=None)], object='list'), expired_at=None, expires_at=1722015590, failed_at=1721929194, finalizing_at=None, in_progress_at=None, metadata={'description': 'nightly eval job'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=0)), Batch(id='batch_NQ9RgzBbLyqfmLOnoBYq0OPG', completion_window='24h', created_at=1721929032, endpoint='/v1/chat/completions', input_file_id='file-900

In [11]:
#reviso puntualmente le batch del clasificador binario

client.batches.retrieve('batch_P0l0BWckYZI3eywp5i2EsT9F')

Batch(id='batch_P0l0BWckYZI3eywp5i2EsT9F', completion_window='24h', created_at=1721926976, endpoint='/v1/chat/completions', input_file_id='file-iMRvNWkQshgCajglZzCHiY1g', object='batch', status='completed', cancelled_at=None, cancelling_at=None, completed_at=1721928895, error_file_id=None, errors=None, expired_at=None, expires_at=1722013376, failed_at=None, finalizing_at=1721928199, in_progress_at=1721926984, metadata={'description': 'nightly eval job'}, output_file_id='file-7wuWx94UJvC2WzN8EoTYUm7R', request_counts=BatchRequestCounts(completed=11343, failed=0, total=11343))

In [16]:
file_response = client.files.content("file-7wuWx94UJvC2WzN8EoTYUm7R")


'{"id": "batch_req_0nwroyc3vVnVNx5XZxLfpYpy", "custom_id": "397703", "response": {"status_code": 200, "request_id": "2af87547f4782460fa8d196199782683", "body": {"id": "chatcmpl-9ow9wUVk6FJZCpaU3LO5Z3ohe8ikv", "object": "chat.completion", "created": 1721926992, "model": "gpt-4o-mini-2024-07-18", "choices": [{"index": 0, "message": {"role": "assistant", "content": "Hateful"}, "logprobs": null, "finish_reason": "stop"}], "usage": {"prompt_tokens": 51, "completion_tokens": 2, "total_tokens": 53}, "system_fingerprint": "fp_661538dc1f"}}, "error": null}\n{"id": "batch_req_Md0fkAKaI7HZ8GVga1VORaRC", "custom_id": "397704", "response": {"status_code": 200, "request_id": "813aeaed465d32f541c8ed21454123a9", "body": {"id": "chatcmpl-9ow9vq55SyFvjZA4CKArkAnmoR9q4", "object": "chat.completion", "created": 1721926991, "model": "gpt-4o-mini-2024-07-18", "choices": [{"index": 0, "message": {"role": "assistant", "content": "No es un comentario odioso."}, "logprobs": null, "finish_reason": "stop"}], "usa

https://www.rootstrap.com/blog/quick-guide-for-sending-multiple-requests-to-gpt-with-the-openai-batch-api

In [25]:
batch_job = client.batches.retrieve('batch_P0l0BWckYZI3eywp5i2EsT9F')
status = batch_job.status

In [26]:
if status == "completed":

	output_file_id = batch_job.output_file_id
	# We should check that there are succesfull results
	# It could be the case that all responses are errors.
	if output_file_id:
		outputs = client.files.content(output_file_id).content
		result_file_name = "outputs.jsonl"

		with open(result_file_name, 'wb') as file:
		    file.write(outputs)

In [32]:
with open(result_file_name, 'r') as file:
  for line in file:
      output = json.loads(line.strip())
      gpt_response = output["response"]["body"]["choices"][0]["message"]["content"]
      print(gpt_response)

Se han truncado las últimas 5000 líneas del flujo de salida.
No hay suficiente información en el texto proporcionado para determinar si tiene un carácter de odio o no.
No odioso.
Hateful
No es un comentario odioso.
El texto expresa un sentimiento de desagrado y frustración, por lo que puede considerarse como un comentario lleno de odio.
No hay odio en el texto.
No hay suficiente información en tu mensaje para determinar si es odioso o no. Por favor, proporciona más contexto.
No hay ningún sentimiento de odio en el texto.
No es un comentario odioso.
El texto es de naturaleza negativa y se puede considerar como un lenguaje de odio.
No es un mensaje de odio.
No es un mensaje de odio.
Hateful
No hay un sentimiento de odio en el texto proporcionado.
Hateful
No es un comentario odioso.
No es un mensaje de odio.
No es un mensaje de odio.
No es un mensaje de odio.
No es un comentario de odio.
Hateful
El texto contiene sentimientos de odio.
No hay contenido odioso en el texto proporcionado.
No 

In [20]:
def retrieve_assistant_messages(file):
    """
    Reads the output JSON file from a batch task in GPT and retrieves the ID and content
    of messages from the role 'assistant'.

    Args:
        file_path (str): The path to the JSON file.

    Returns:
        list: A list of dictionaries with 'custom_id' and 'content' from the role 'assistant'.
    """
   # with open(file_path, 'r') as f:
    #    data = json.load(f)

    assistant_messages = []

    for entry in file:
        custom_id = entry.get('custom_id')
        messages = entry.get('messages', [])

        for message in messages:
            if message.get('role') == 'assistant':
                content = message.get('content')
                assistant_messages.append({'custom_id': custom_id, 'content': content})

    return assistant_messages

In [21]:

assistant_messages = retrieve_assistant_messages(file_response)

TypeError: 'HttpxBinaryResponseContent' object is not iterable

In [ ]:
sentiment = response.choices[0].message.content.strip().lower()

In [ ]:
# Save the batch to a .jsonl file
with open('batch_gpt_bin_v1.jsonl', 'w') as f:
    for entry in batch:
        json.dump(entry, f)
        f.write('\n')

print("Batch file created successfully in .jsonl format!")

Batch file created successfully in .jsonl format!


In [ ]:
batch_input_file = client.files.create(
  file=open("batch_gpt_bin_v1.jsonl", "rb"),
  purpose="batch"
)

In [ ]:
batch_input_file

FileObject(id='file-iMRvNWkQshgCajglZzCHiY1g', bytes=4815341, created_at=1721926964, filename='batch_gpt_bin_v1.jsonl', object='file', purpose='batch', status='processed', status_details=None)

In [ ]:
batch_input_file_id = 'file-iMRvNWkQshgCajglZzCHiY1g'

client.batches.create(
    input_file_id=batch_input_file_id,
    endpoint="/v1/chat/completions",
    completion_window="24h",
    metadata={
      "description": "nightly eval job"
    }
)

Batch(id='batch_P0l0BWckYZI3eywp5i2EsT9F', completion_window='24h', created_at=1721926976, endpoint='/v1/chat/completions', input_file_id='file-iMRvNWkQshgCajglZzCHiY1g', object='batch', status='validating', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1722013376, failed_at=None, finalizing_at=None, in_progress_at=None, metadata={'description': 'nightly eval job'}, output_file_id=None, request_counts=BatchRequestCounts(completed=0, failed=0, total=0))

In [ ]:
client.batches.retrieve('batch_P0l0BWckYZI3eywp5i2EsT9F')

Batch(id='batch_P0l0BWckYZI3eywp5i2EsT9F', completion_window='24h', created_at=1721926976, endpoint='/v1/chat/completions', input_file_id='file-iMRvNWkQshgCajglZzCHiY1g', object='batch', status='in_progress', cancelled_at=None, cancelling_at=None, completed_at=None, error_file_id=None, errors=None, expired_at=None, expires_at=1722013376, failed_at=None, finalizing_at=None, in_progress_at=1721926984, metadata={'description': 'nightly eval job'}, output_file_id=None, request_counts=BatchRequestCounts(completed=1131, failed=0, total=11343))